In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import IPython.display as ipd

import os
import json
import math
import torch
from torch import nn
from torch.nn import functional as F
from torch.utils.data import DataLoader

import commons
import utils
from data_utils import TextAudioSpeakerLoader, TextAudioSpeakerCollate
from models import SynthesizerTrn
from text.symbols import symbols
from text import text_to_sequence

from scipy.io.wavfile import write
import numpy as np


def get_text(text, hps):
    text_norm = text_to_sequence(text, hps.data.text_cleaners)
    if hps.data.add_blank:
        text_norm = commons.intersperse(text_norm, 0)
    text_norm = torch.LongTensor(text_norm)
    return text_norm

In [2]:
hps = utils.get_hparams_from_file("./configs/vtubers.json")

In [5]:
net_g = SynthesizerTrn(
    len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    n_speakers=hps.data.n_speakers,
    **hps.model)
_ = net_g.eval()

_ = utils.load_checkpoint("/Users/xingyijin/Downloads/G_6400.pth", net_g, None)

INFO:root:Loaded checkpoint '/Users/xingyijin/Downloads/G_6400.pth' (iteration 21)
Loaded checkpoint '/Users/xingyijin/Downloads/G_6400.pth' (iteration 21) 


In [35]:
all_emotions = np.load("all_emotions.npy")
emotion_dict = {
    "小声": "nen104_220.wav",
    "激动": "nen001_065.wav",
    "平静1": "nen005_110.wav",
    "平静2": "nen113_082.wav"
}
import random
def tts(txt, emotion):
    stn_tst = get_text(txt, hps)
    with torch.no_grad():
        x_tst = stn_tst.unsqueeze(0)
        x_tst_lengths = torch.LongTensor([stn_tst.size(0)])
        sid = torch.LongTensor([4])
        if emotion == "random":
            emo = torch.randn([1,1024])
        elif emotion == "random_sample":
            emo = torch.FloatTensor(all_emotions[random.randint(0, all_emotions.shape[0])]).unsqueeze(0)
        elif emotion.endswith("wav"):
            emo = torch.FloatTensor(np.load(f"/Users/xingyijin/Downloads/emo/{emotion}.emo.npy")).unsqueeze(0)
        else:
            emo = torch.FloatTensor(np.load(f"/Users/xingyijin/Downloads/emo/{emotion_dict[emotion]}.emo.npy")).unsqueeze(0)

        audio = net_g.infer(x_tst, x_tst_lengths, sid=sid, noise_scale=.667, noise_scale_w=0.8, length_scale=1, emo=emo)[0][0,0].data.float().numpy()
    ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate, normalize=False))

In [13]:
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
# tts(txt, "nen001_042")
tts(txt, emotion="小声")
tts(txt, emotion="激动")
tts(txt, emotion="平静1")
tts(txt, emotion="平静2")


In [17]:
txt = "こんにちは。私わあやちねねです。"
tts(txt, emotion="nen104_220.wav")
tts(txt, emotion="nen001_065.wav")
tts(txt, emotion="nen005_110.wav")
# tts(txt, emotion="nen113_082.wav")

In [15]:
txt = "授業中に出したら、学校生活終わるなり。"
tts(txt, emotion="nen104_220.wav")
tts(txt, emotion="nen001_065.wav")
tts(txt, emotion="nen005_110.wav")
tts(txt, emotion="nen113_082.wav")

In [34]:
txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')
tts(txt, emotion='random_sample')

In [22]:

txt = "なんでこんなに慣れてんのよ。私の方が先に好きだったのに"
tts(txt, emotion='random')
tts(txt, emotion='random')
tts(txt, emotion='random')
tts(txt, emotion='random')
tts(txt, emotion='random')
tts(txt, emotion='random')


### Voice Conversion

In [ ]:
dataset = TextAudioSpeakerLoader(hps.data.validation_files, hps.data)
collate_fn = TextAudioSpeakerCollate()
loader = DataLoader(dataset, num_workers=8, shuffle=False,
    batch_size=1, pin_memory=True,
    drop_last=True, collate_fn=collate_fn)
data_list = list(loader)

In [ ]:
with torch.no_grad():
    x, x_lengths, spec, spec_lengths, y, y_lengths, sid_src = [x.cuda() for x in data_list[0]]
    sid_tgt1 = torch.LongTensor([1]).cuda()
    sid_tgt2 = torch.LongTensor([2]).cuda()
    sid_tgt3 = torch.LongTensor([4]).cuda()
    audio1 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt1)[0][0,0].data.cpu().float().numpy()
    audio2 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt2)[0][0,0].data.cpu().float().numpy()
    audio3 = net_g.voice_conversion(spec, spec_lengths, sid_src=sid_src, sid_tgt=sid_tgt3)[0][0,0].data.cpu().float().numpy()
print("Original SID: %d" % sid_src.item())
ipd.display(ipd.Audio(y[0].cpu().numpy(), rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt1.item())
ipd.display(ipd.Audio(audio1, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt2.item())
ipd.display(ipd.Audio(audio2, rate=hps.data.sampling_rate, normalize=False))
print("Converted SID: %d" % sid_tgt3.item())
ipd.display(ipd.Audio(audio3, rate=hps.data.sampling_rate, normalize=False))

In [29]:
all_emo = []
import os
for npyname in sorted(os.listdir("/Users/xingyijin/Downloads/emo")):
    if npyname.endswith("emo.npy"):
        all_emo.append(np.load(f"/Users/xingyijin/Downloads/emo/{npyname}").reshape([1,-1]))
all_emotions = np.concatenate(all_emo, axis=0)

In [30]:
np.save("all_emotions.npy", all_emotions)